# Linear Camera Model

This notebook is a study about the linear camera model (or pinhole model) using *CoppeliaSim* as a simulator to verify results in a virtual environment. 

The goal is to verify if the data generated between math and simulation is coherent. For this:
1. Instanciate a Vision Sensor in both *CoppeliaSim* and in a Mathematical Model that have matched parameters;
2. Create a 3D scene with detectable points in the space in both environments;
3. Realize perspective projection calculation in the Mathematical Model;
4. Detect where the points lie in the *CoppeliaSim*'s Vision Sensor image;
5. Check if results match. 

If the results are matching for any position, then the Mathematical Model fit with *CoppeliaSim*'s image render. 

---

In [32]:
# Importing modules...
import numpy as np
import cv2

import sys
sys.path.append('../..') # Go back to base directory

from modules.plot.viewer2d import Viewer2D
from modules.plot.viewer3d import Viewer3D

from modules.vision.blob_detection import detect_blobs

from modules.math.utils import cube

from coppeliasim_zmqremoteapi_client import RemoteAPIClient

# Init client 
client = RemoteAPIClient()    # Client object 
sim = client.getObject('sim') # Simulation object

# Building the Intrinsic Matrix

The **Intrinsic Matrix** is responsible for encoding the camera's internal parameters and how it projects points in the 3D scene to the 2D image plane.

The parameters encoded in the matrix are:
- $x$ and $y$ focal distances in pixels;
- Image plane's principle point.

Also called **Camera Matrix**, it is defined as:

$$K = \begin{bmatrix}
        f_x & 0   & c_x \\
        0   & f_y & c_y \\
        0   & 0   & 1
      \end{bmatrix}$$

The focal distances in pixels are given by:

$$f_x = \frac{R_x}{2\cdot\tan(\frac{\alpha}{2})}$$
$$f_y = \frac{R_y}{2\cdot\tan(\frac{\alpha}{2})}$$

And need to be adjusted as such:

$$\begin{cases} f_y = f_y \cdot\frac{R_x}{R_y}, \text{if} \space\frac{R_x}{R_y} > 1 \\
                f_x = f_x \cdot\frac{R_y}{R_x}, \text{if} \space\frac{R_x}{R_y} < 1 \end{cases}$$

And the principle point coordinates are:
$$c_x = \frac{R_x}{2}$$
$$c_y = \frac{R_y}{2}$$

---

In [33]:
# Declare intrinsic parameters
fov_degrees = 60.0
resolution = (720, 720)

# Generate intrinsic parameters matrix
fov_radians = np.radians(fov_degrees)

# Focal distances in pixels
f_x = resolution[0]/(2*np.tan(fov_radians/2))
f_y = resolution[1]/(2*np.tan(fov_radians/2))

aspect_ratio = resolution[0]/resolution[1]

# Aspect ratio scaling
if aspect_ratio > 1: # Landscape
    f_y *= aspect_ratio
if aspect_ratio < 1: # Portrait
    f_x /= aspect_ratio

# Principle point
c_x, c_y = resolution[0]/2, resolution[1]/2

intrinsic_matrix = np.array([[f_x,   0, c_x],
                             [  0, f_y, c_y],
                             [  0,   0,   1]])

# Building the Extrinsic Matrix

The **Extrinsic Matrix** encodes the Rotation $R$ and Translation $t$ of the camera frame in a homogeneous transformation:

$$\begin{bmatrix}
    R & t \\
    0 & 1 
\end{bmatrix}_{4\times4}$$

For convenience, the Extrinsic Matrix can be treated as a ${3\times4}$ matrix:

$$\begin{bmatrix}
    R \ | \ t
\end{bmatrix}_{3\times4}$$

The Extrinsic Matrix will be extracted from CoppeliaSim's `sim.getObjectMatrix` API function.

In this model, the $z$-axis must be pointed forward in the optical axis. Looking from behind the camera, the $x$-axis msut be pointing right, and the $y$-axis must be pointing down, just like the image plane. 

---

In [34]:
# Get the vision sensor handle
vision_sensor_handle = sim.getObject('/VisionSensor') 

# Get Coppelia's 3x4 object matrix
object_matrix = np.array(sim.getObjectMatrix(vision_sensor_handle)).reshape((3,4))

R, t = object_matrix[:, :-1], object_matrix[:, [-1]] # Get 3x3 matrix and 3x1 matrix from 3x4 matrix

# X and Y axis of Coppelia's Vision Sensor are inverted
R[:,0] *= -1
R[:,1] *= -1

# Generate extrinsic parameters matrix
extrinsic_matrix = np.vstack((np.hstack((R, t)), np.array([0, 0, 0, 1])))

# Setting up and Plotting the 3D Scene

For setting up the scene, there will be a set of 3D points scattered across the Mathematical Model and *CoppeliaSim*'s environment.

---

In [35]:
# 3D points to be projected
world_points = cube() # Vertices of a cube

# Change cube position
world_points[0] -= 0.25
world_points[1] -= 0.25
world_points[2] += 1

# Create the Scene Viewer
scene = Viewer3D(title='Camera Pose Scene', 
                 size=5)

# Add elements to the scene
scene.add_frame(np.eye(4), 'World Frame', axis_size=0.2)
scene.add_frame(extrinsic_matrix, 'Camera Frame', axis_size=0.2) 
scene.add_points(world_points, 'World Points', 'black')

# Plot scene
scene.figure.show(renderer='notebook_connected')

# Perspective Projection

The projection of a 3D Point in the World Frame $P_w$ to a pixel coordinate in the image plane $p_c$ is done by:

$$p_c = \begin{bmatrix}
           K \ | \ 0
        \end{bmatrix}_{3\times4} \cdot \begin{bmatrix}
                                          R & t \\
                                          0 & 1 
                                       \end{bmatrix}_{4\times4}^{-1} \cdot P_w
$$

After $p_c$ is obtained, the points will be:
1. Normalized, because they are in homogeneous coordinates;
2. Discarded the last row for 2D points;
3. Casted as intergers, as there are an interger number of pixels.

---

In [36]:
# Generate perspective projection matrix
# Convert intrinsic matrix to 3x4 size and invert the extrinsic parameters
projection_matrix = np.hstack((intrinsic_matrix, np.zeros((3,1)))) @ np.linalg.inv(extrinsic_matrix) 

# Project the 3D point with the new pose
world_points_h = np.vstack((world_points, np.ones(world_points.shape[1]))) # Convert to homogeneous
projected_points = projection_matrix @ world_points_h # Project points to plane
projected_points /= projected_points[-1] # Normalize homogeneous coordinates
projected_points = projected_points[:-1, :] # Discard the last row

# Plotting the 2D Projected Scene

The 3D points will be plotted as 2D projected points in image space. 

---

In [37]:
# Create the image viewer
projection = Viewer2D(title='Linear Model Projection', 
                      resolution=resolution, 
                      graphical=True)

# Adding the projected points to the image
projection.add_points(points=projected_points, 
                      name='Projected Points', 
                      color='black')

# Plot projected points
projection.figure.show(renderer='notebook_connected')

# Detecting the Blobs' Centroids in Coppelia's Image Feed

To detect the point cloud in *CoppeliaSim*, the following process will be followed:

1. Retrieve VisionSensor image with `sim.getVisionSensorImg`;
2. Get centroids of each blob.

---

In [38]:
# When simulation is not running, ZMQ message handling could be a bit
# slow, since the idle loop runs at 8 Hz by default.
# Setting the idle loop to run at full speed for this program
defaultIdleFps = sim.getInt32Param(sim.intparam_idle_fps)   
sim.setInt32Param(sim.intparam_idle_fps, 0)

# Simulation begins here
sim.startSimulation()

point_cloud_handle = sim.createPointCloud(1, 1, 8, 3)
markers_color = list([255,255,255]) # White

# Insert points into point cloud
points = np.concatenate(world_points.T)
point_count = sim.insertPointsIntoPointCloud(point_cloud_handle, 0, points, markers_color)

blob_centroids = None

image_pinhole = None # Image will be stored here

# Retrieve images
while (t := sim.getSimulationTime()) < 5:
    # Get grayscale image buffer
    buffer, resolution = sim.getVisionSensorImg(vision_sensor_handle, 1) # Set second argument to 1 for grayscale, 0 for RGB

    # Convert buffer into single channel image
    image_unflipped = np.frombuffer(buffer, dtype=np.uint8).reshape(resolution[1], resolution[0])

    # In CoppeliaSim images are left to right (x-axis), and bottom to top (y-axis)
    # This is consistent with the axes of vision sensors, pointing Z outwards, Y up
    image_pinhole = cv2.flip(image_unflipped, 0)

    # Wait for images to come up and check if they're not black images 
    if image_pinhole is not None and np.any(image_pinhole): 
        break # Stop on the first valid image

# Simple blob detection method
blob_centroids = detect_blobs(image_pinhole)

# Restore the original idle loop frequency:
sim.setInt32Param(sim.intparam_idle_fps, defaultIdleFps)

# Simulation ends here
sim.stopSimulation()

# Calculating the Projection Error

To compare the projected points to the detected blobs' location, point to point distance will be calculated, and the shortest distance (in pixels) will be assumed as the projection error for a match.

---

In [39]:
projection_errors = []
for blob_centroid in blob_centroids.T:
    distances = [] # Distances of the projected point to the blob centroid positions in the image

    for projected_point in projected_points.T:
        distances.append(np.linalg.norm(projected_point - blob_centroid)) # Minimum distance of the projected point to the blob centroid 

    projection_error = np.min(distances) # In pixels
    projection_errors.append(projection_error)

projection_errors = np.array(projection_errors)

# Comparing Projected Points to Detected Blobs' Centroids

Now the projected points will be plotted along with the detected blob centroids for comparison. The projected points will be colored by their projection error.

---

In [40]:
# Create the image viewer
plot = Viewer2D(title='Coppelia\'s Vision Sensor', 
                resolution=resolution, 
                image=image_pinhole,
                graphical=True)

# Green to yellow to red color scale to represent undistortion error
error_corlorscale =  [[0.0, 'rgb(0,  255,0)'], # Green
                      [0.5, 'rgb(255,255,0)'], # Yellow
                      [1.0, 'rgb(255,  0,0)']] # Red

# Adding the detected blobs to the image
plot.add_points(points=blob_centroids, 
                name='Blob Centroids', 
                color='white')

# Adding the projected points to the image
plot.add_points(points=projected_points,
                name='Projected Points', 
                color=projection_errors,          # Parameter that defines color of each point
                colorscale=error_corlorscale,     # Color scale of points
                range=[0, 1.8],                   # Range of the color values
                colorbar='Projection Error (px)') # Color bar title

# Plot image
plot.figure.show(renderer='notebook_connected')

# Mean projection error
print(f'Mean Projection Error: {np.mean(projection_errors):.2f} px')

Mean Projection Error: 0.63 px
